In [2]:
print("Hello World")

Hello World


In [3]:
!pip install tqdm

  Obtaining dependency information for tqdm from https://files.pythonhosted.org/packages/d0/30/dc54f88dd4a2b5dc8a0279bdd7270e735851848b762aeb1c1184ed1f6b14/tqdm-4.67.1-py3-none-any.whl.metadata
     ---------------------------------------- 0.0/57.7 kB ? eta -:--:--
     ---------------------------------------- 57.7/57.7 kB 1.5 MB/s eta 0:00:00
   ---------------------------------------- 0.0/78.5 kB ? eta -:--:--
   ---------------------------------------- 78.5/78.5 kB 4.3 MB/s eta 0:00:00



[notice] A new release of pip is available: 23.2.1 -> 25.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [1]:
!pip install tensorflow opencv-python mediapipe

  Obtaining dependency information for tensorflow from https://files.pythonhosted.org/packages/f9/37/b97abb360b551fbf5870a0ee07e39ff9c655e6e3e2f839bc88be81361842/tensorflow-2.20.0-cp312-cp312-win_amd64.whl.metadata
  Obtaining dependency information for opencv-python from https://files.pythonhosted.org/packages/fa/80/eb88edc2e2b11cd2dd2e56f1c80b5784d11d6e6b7f04a1145df64df40065/opencv_python-4.12.0.88-cp37-abi3-win_amd64.whl.metadata
  Obtaining dependency information for mediapipe from https://files.pythonhosted.org/packages/b7/79/b77808f8195f229ef0c15875540dfdd36724748a4b3de53d993f23336839/mediapipe-0.10.21-cp312-cp312-win_amd64.whl.metadata
  Obtaining dependency information for absl-py>=1.0.0 from https://files.pythonhosted.org/packages/8f/aa/ba0014cc4659328dc818a28827be78e6d97312ab0cb98105a770924dc11e/absl_py-2.3.1-py3-none-any.whl.metadata
  Obtaining dependency information for astunparse>=1.6.0 from https://files.pythonhosted.org/packages/2b/03/13dde6512ad7b4557eb792fbcf0c653af60


[notice] A new release of pip is available: 23.2.1 -> 25.2
[notice] To update, run: python.exe -m pip install --upgrade pip


In [2]:
import cv2
import mediapipe as mp

# Inicializar MediaPipe Hands
mp_hands = mp.solutions.hands
hands = mp_hands.Hands(static_image_mode=False, max_num_hands=1, min_detection_confidence=0.5)
mp_drawing = mp.solutions.drawing_utils

# Iniciar captura de video
cap = cv2.VideoCapture(0)

print("Entorno verificado. Presione 'q' para salir.")

while cap.isOpened():
    success, image = cap.read()
    if not success:
        print("Ignorando fotograma de cámara vacío.")
        continue

    # Convertir la imagen a RGB para MediaPipe
    image = cv2.cvtColor(cv2.flip(image, 1), cv2.COLOR_BGR2RGB)
    image.flags.writeable = False
    results = hands.process(image)

    # Dibujar las anotaciones de la mano en la imagen
    image.flags.writeable = True
    image = cv2.cvtColor(image, cv2.COLOR_RGB2BGR)
    if results.multi_hand_landmarks:
        for hand_landmarks in results.multi_hand_landmarks:
            # Imprimir coordenadas del punto de referencia de la muñeca (landmark 0)
            print(f'Coordenadas de la muñeca: {hand_landmarks.landmark}')
            mp_drawing.draw_landmarks(
                image,
                hand_landmarks,
                mp_hands.HAND_CONNECTIONS)
    
    cv2.imshow('Verificacion de MediaPipe', image)
    if cv2.waitKey(5) & 0xFF == ord('q'):
        break

cap.release()
cv2.destroyAllWindows()

Entorno verificado. Presione 'q' para salir.
Coordenadas de la muñeca: [x: 0.745696247
y: 1.04914904
z: 4.76643947e-007
, x: 0.690634966
y: 1.01927912
z: -0.00925501622
, x: 0.656172335
y: 0.964740634
z: -0.0259607043
, x: 0.632247806
y: 0.928079367
z: -0.0411254652
, x: 0.61309886
y: 0.898972273
z: -0.0600701161
, x: 0.661562204
y: 0.895043314
z: -0.0600534119
, x: 0.614465714
y: 0.798136115
z: -0.0908295289
, x: 0.580672562
y: 0.733536601
z: -0.109886855
, x: 0.551625
y: 0.688130677
z: -0.121981777
, x: 0.707740784
y: 0.882360816
z: -0.0730039775
, x: 0.673077822
y: 0.775890589
z: -0.0996733159
, x: 0.651611805
y: 0.709568
z: -0.115042627
, x: 0.632206082
y: 0.65833205
z: -0.124599531
, x: 0.759533644
y: 0.892936051
z: -0.083833009
, x: 0.742670178
y: 0.780542254
z: -0.112464391
, x: 0.733650267
y: 0.708170176
z: -0.124561325
, x: 0.724429
y: 0.651561201
z: -0.131172493
, x: 0.810413361
y: 0.919580698
z: -0.0929147378
, x: 0.817974269
y: 0.846972287
z: -0.120629355
, x: 0.823442578
y

In [ ]:
import os
import cv2
import mediapipe as mp
import numpy as np
from tqdm import tqdm

# --- 1. CONFIGURACIÓN INICIAL ---

# Inicializa la solución de MediaPipe Hands.
mp_hands = mp.solutions.hands
hands = mp_hands.Hands(static_image_mode=True, max_num_hands=1, min_detection_confidence=0.5)

# --- RUTAS Y PARÁMETROS ---
# ¡IMPORTANTE! Asegúrate de que esta ruta apunte a tu carpeta de imágenes originales.
SOURCE_DIR = './datos'
# Nombre de la carpeta donde se guardarán las nuevas imágenes procesadas.
TARGET_DIR = './datos_procesados'
# Tamaño al que se redimensionarán todas las imágenes (ancho y alto).
IMG_SIZE = 224
# Un pequeño margen (en píxeles) para añadir alrededor de la mano al recortar.
PADDING = 20

# Crea el directorio de destino si no existe.
os.makedirs(TARGET_DIR, exist_ok=True)

print(f"Iniciando el preprocesamiento de imágenes para el Enfoque B (CNN).")
print(f"Las imágenes procesadas se guardarán en: '{TARGET_DIR}'")

# --- 2. PROCESAMIENTO: DETECCIÓN, RECORTE Y REDIMENSIÓN ---

# Itera sobre cada carpeta de letras en el directorio de origen.
for label in sorted(os.listdir(SOURCE_DIR)):
    source_label_path = os.path.join(SOURCE_DIR, label)
    
    # Asegurarse de que es un directorio.
    if not os.path.isdir(source_label_path):
        continue
        
    # Crea la carpeta correspondiente en el directorio de destino.
    target_label_path = os.path.join(TARGET_DIR, label)
    os.makedirs(target_label_path, exist_ok=True)
    
    # Usamos tqdm para mostrar una barra de progreso.
    image_files = os.listdir(source_label_path)
    for img_file in tqdm(image_files, desc=f'Procesando letra "{label}"'):
        source_img_path = os.path.join(source_label_path, img_file)
        
        # Lee la imagen original.
        img = cv2.imread(source_img_path)
        if img is None:
            print(f"Advertencia: No se pudo leer la imagen {source_img_path}")
            continue
        
        # Obtiene las dimensiones de la imagen original.
        h, w, _ = img.shape
        
        # Convierte la imagen a RGB para MediaPipe.
        img_rgb = cv2.cvtColor(img, cv2.COLOR_BGR2RGB)
        
        # Procesa la imagen para encontrar la mano.
        results = hands.process(img_rgb)
        
        # Si se detectó una mano...
        if results.multi_hand_landmarks:
            # Extrae los puntos de referencia.
            hand_landmarks = results.multi_hand_landmarks
            
            # --- Calcula el cuadro delimitador (bounding box) alrededor de la mano ---
            x_coords = [landmark.x for landmark in hand_landmarks.landmark]
            y_coords = [landmark.y for landmark in hand_landmarks.landmark]
            
            # Convierte las coordenadas normalizadas a píxeles.
            x_min = int(min(x_coords) * w) - PADDING
            y_min = int(min(y_coords) * h) - PADDING
            x_max = int(max(x_coords) * w) + PADDING
            y_max = int(max(y_coords) * h) + PADDING
            
            # Asegurarse de que las coordenadas no se salgan de los límites de la imagen.
            x_min = max(0, x_min)
            y_min = max(0, y_min)
            x_max = min(w, x_max)
            y_max = min(h, y_max)
            
            # --- Recorta la imagen usando el cuadro delimitador ---
            cropped_img = img[y_min:y_max, x_min:x_max]
            
            # Si el recorte es válido (no está vacío)...
            if cropped_img.size > 0:
                # --- Redimensiona la imagen recortada al tamaño estándar ---
                resized_img = cv2.resize(cropped_img, (IMG_SIZE, IMG_SIZE))
                
                # --- Guarda la imagen procesada en la carpeta de destino ---
                target_img_path = os.path.join(target_label_path, img_file)
                cv2.imwrite(target_img_path, resized_img)

print("\nProcesamiento completado.")
hands.close()

print(f"\n¡Éxito! Se ha creado un nuevo dataset de imágenes procesadas en '{TARGET_DIR}'.")